# GeoPandas: Pandas + geometry data type + custom geo goodness

Notebook downloaded from: https://geohackweek.github.io/vector/04-geopandas-intro/

I modifyed it to fit the Databricks running environment

You can find more Geopandas at http://geopandas.org/

## 1. Background

[GeoPandas](http://geopandas.org) adds a spatial geometry data type to `Pandas` and enables spatial operations on these types, using [shapely](http://toblerity.org/shapely/). GeoPandas leverages Pandas together with several core open source geospatial packages and practices to provide a uniquely simple and convenient framework for handling geospatial feature data, operating on both geometries and attributes jointly, and as with Pandas, largely eliminating the need to iterate over features (rows). Also as with Pandas, it adds a very convenient and fine-tuned plotting method, and read/write methods that handle multiple file and "serialization" formats.

**_NOTES:_**
- Like `shapely`, these spatial data types are limited to discrete entities/features and do not address continuously varying rasters or fields.
- While GeoPandas spatial objects can be assigned a Coordinate Reference System (`CRS`), operations can not be performed across CRS's. Plus, geodetic ("unprojected", lat-lon) CRS are not handled in a special way; the area of a geodetic polygon will be in degrees. (We need CRSs, because we'll work with maps and geographical data, and it makes a huge difference, whether the coordinates are in degrees as with e.g. the GPS or in meters, or in any other units.)

GeoPandas is still fairly young, but it builds on mature and stable and widely used packages (Pandas, shapely, etc). Expect continued growth, and possibly some kinks.

**When should you use GeoPandas?**
- For exploratory data analysis, including in Jupyter notebooks.
- For highly compact and readable code. Which in turn improves reproducibility.
- If you're comfortable with Pandas, R dataframes, or tabular/relational approaches.

**When it may not be the best tool?**
- For polished map creation and multi-layer, interactive visualization; if you're comfortable with GIS, use a desktop GIS like QGIS! You can generate intermediate GIS files and plots with GeoPandas, then shift over to QGIS. Or refine the plots in Python with matplotlib or additional packages.
- If you need high performance, though I'm not completely sure. Performance increased recently and substantial enhancements are in the works (including possibly a [Dask](http://dask.pydata.org) parallelization implementation.

## 2. Set up packages and data file path

First you need to install geopandas on your cluster

In [8]:
%%bash
/databricks/python/bin/pip install geopandas

In [9]:
'''%matplotlib inline; the tutorial uses this magic comment that does not work on Databricks, we'll use something else instead'''

from __future__ import (absolute_import, division, print_function)
import os

import matplotlib as mpl
import matplotlib.pyplot as plt
# The two statemens below are used mainly to set up a plotting
# default style that's better than the default from Matplotlib 1.x
# Matplotlib 2.0 supposedly has better default styles.
import seaborn as sns
plt.style.use('bmh')

from shapely.geometry import Point
import pandas as pd
import geopandas as gpd
from geopandas import GeoSeries, GeoDataFrame

In [10]:
mpl.__version__, pd.__version__, gpd.__version__

## 3. GeoSeries: The geometry building block

Like a Pandas `Series`, a `GeoSeries` is the building block for the more broadly useful and powerful `GeoDataFrame` that we'll focus on in this tutorial. Here we'll first take a bit of time to examine a `GeoSeries`.

A `GeoSeries` is made up of an index and a GeoPandas `geometry` data type. This data type is a [shapely.geometry object](http://toblerity.org/shapely/manual.html#geometric-objects), and therefore inherits their attributes and methods such as `area`, `bounds`, `distance`, etc.

GeoPandas has six classes of **geometric objects**, corresponding to the three basic single-entity geometric types and their associated homogeneous collections of multiple entities:
- **Single entity (core, basic types):**
  - Point
  - Line (*formally known as a LineString*)
  - Polygon
- **Homogeneous entity collections:**
  - Multi-Point
  - Multi-Line (*MultiLineString*)
  - Multi-Polygon

A `GeoSeries` is then a list of geometry objects and their associated index values.

**_NOTE/WATCH:_**   
Entries (rows) in a GeoSeries can store different geometry types; GeoPandas does not constrain the geometry column to be of the same geometry type. This can lead to unexpected problems if you're not careful! Specially if you're used to thinking of a GIS file format like shape files, which store a single geometry type. Also beware that certain export operations (say, to shape files ...) will fail if the list of geometry objects is heterogeneous.

But enough theory! Let's get our hands dirty (so to speak) with code. We'll start by illustrating how GeoSeries are constructured.

### Create a `GeoSeries` from a list of `shapely Point` objects using the `Point` constructor

In [17]:
gs = GeoSeries([Point(-120, 45), Point(-121.2, 46), Point(-122.9, 47.5)])
gs

In [18]:
type(gs), len(gs)

A GeoSeries (and a GeoDataFrame) can store a CRS implicitly associated with the geometry column. This is useful as essential spatial metadata and for transformation (reprojection) to another CRS. Let's assign the CRS.

In [20]:
gs.crs = {'init': 'epsg:4326'}

The `plot` method accepts standard `matplotlib.pyplot` style options, and can be tweaked like any other `matplotlib` figure.

*Note: There may be something odd happening with plot `markersize` ...*

Now this is a bit more complicated in Databricks. Original code below (does not work if you try to run it).

In [24]:
gs.plot(marker='*', color='red', markersize=100, figsize=(4, 4))
plt.xlim([-123, -119.8])
plt.ylim([44.8, 47.7]);

In Databricks you can only plot with the "display" command. See the workaround below. (Note the "ax=ax" in the function arguments that specifies that the axes to plot to should be the one we created.)

In [26]:
fig, ax = plt.subplots()
gs.plot(marker='*', color='red', markersize=100, ax=ax, figsize=(4, 4))
plt.xlim([-123, -119.8])
plt.ylim([44.8, 47.7])

display(fig)

**Let's get a bit fancier, as a stepping stone to GeoDataFrames.** First, we'll define a simple dictionary of lists, that we'll use again later.

In [28]:
data = {'name': ['a', 'b', 'c'],
        'lat': [45, 46, 47.5],
        'lon': [-120, -121.2, -122.9]}

Note this convenient, compact approach to create a list of `Point` shapely objects out of X & Y coordinate lists:

In [30]:
geometry = [Point(xy) for xy in zip(data['lon'], data['lat'])]
geometry

We'll wrap up by creating a GeoSeries where we explicitly define the index values.

In [32]:
gs = GeoSeries(geometry, index=data['name'])
gs

## 4. GeoDataFrames: The real power tool

**_NOTE/HIGHLIGHT:_**   
- It's worth noting that a GeoDataFrame can be described as a *Feature Collection*, where each row is a *Feature*, a *geometry* column is defined (thought the name of the column doesn't have to be "geometry"), and the attribute *Properties* includes the other columns (the Pandas DataFrame part, if you will).
- More than one column can store geometry objects! We won't explore this capability in this tutorial.

### Start with a simple, manually constructed illustration

We'll build on the GeoSeries examples. Let's reuse the `data` dictionary we defined earlier, this time to create a DataFrame.

In [37]:
df = pd.DataFrame(data)
df

Now we use the DataFrame and the "list-of-shapely-Point-objects" approach to create a GeoDataFrame. Note the use of two DataFrame attribute columns, which are effectively just two simple Pandas Series.

In [39]:
geometry = [Point(xy) for xy in zip(df['lon'], df['lat'])]
gdf = GeoDataFrame(df, geometry=geometry)

There's nothing new to visualize, but this time we're using the `plot` method from a GeoDataFrame, *not* from a GeoSeries. They're not exactly the same thing under the hood.

In [41]:
'''Again, visualization is not that simple'''
fig, ax = plt.subplots()
gdf.plot(marker='*', color='green', markersize=50, ax=ax, figsize=(3, 3))
plt.xlim([-123, -119.8])
plt.ylim([44.8, 47.7])

display(fig)

### FINALLY, we get to work with real data! Load and examine the simple "oceans" shape file

`gpd.read_file` is the workhorse for reading GIS files. It leverages the [fiona](http://toblerity.org/fiona/README.html) package.

First click "Download ocean" here: http://www.naturalearthdata.com/downloads/10m-physical-vectors/10m-ocean/

(Do not unzip.)

Upload the file to Databricks and remember the path. Mine was uploaded as: /FileStore/tables/noq9c6781505671582420/ne_10m_ocean.zip

To load the map, we do not only need the .shp file but also the others coming with it. But if we'd unzip, we'd have to upload all files separately and Databricks would put them at random locations. Fortunately we can use the .zip file as a virtual drive, and load the .shp file from there, and there will be no problam with loading the rest of the files either. (When you run the code below, remember to switch the file path to the path where Databricks uploaded the file for you.)

In [46]:
oceans = gpd.read_file('/ne_10m_ocean.shp',vfs='zip:///dbfs/FileStore/tables/noq9c6781505671582420/ne_10m_ocean.zip')

In [47]:
oceans.head()

The `crs` was read from the shape file's `prj` file:

In [49]:
oceans.crs

Now we finally plot a real map (or blobs, depending on your aesthetics), from a dataset that's global-scale and stored in "geographic" (latitude & longitude) coordinates. It's *not* the actual ocean shapes defined by coastal boundaries, but bear with me. A colormap has been applied to distinguish the different Oceans.

In [51]:
'''I know, plotting again... Whould be so much easier outside Databricks, but most probably your computer wouldn't have enough computing power to solve the actual exercise on the workshop.'''
fig, ax = plt.subplots()
oceans.plot(cmap='Set2', ax=ax, figsize=(10, 10));

display(fig)

`oceans.shp` stores both `Polygon` and `Multi-Polygon` geometry types (a `Polygon` may also be viewed as a `Multi-Polygon` with 1 member). We can get at the geometry types and other geometry properties easily.

In [53]:
oceans.geom_type

In [54]:
# Beware that these area calculations are in degrees, which is fairly useless
oceans.geometry.area

In [55]:
oceans.geometry.bounds

### Load "Natural Earth" countries dataset, bundled with GeoPandas
*"[Natural Earth](http://www.naturalearthdata.com) is a public domain map dataset available at 1:10m, 1:50m, and 1:110 million scales. Featuring tightly integrated vector and raster data, with Natural Earth you can make a variety of visually pleasing, well-crafted maps with cartography or GIS software."* A subset comes bundled with GeoPandas and is accessible from the `gpd.datasets` module. We'll use it as a helpful global base layer map.

Click "Download countries": http://www.naturalearthdata.com/downloads/10m-cultural-vectors/10m-admin-0-countries/

And then same procedure with uploading the .zip file. (Remember to change the file path, when you run the code below.)

In [58]:
world = gpd.read_file('/ne_10m_admin_0_countries.shp',vfs='zip:///dbfs/FileStore/tables/b87an3dx1505673052147/ne_10m_admin_0_countries.zip')
world.head(2)

Its CRS is also EPSG:4326:

In [60]:
world.crs

In [61]:
fig, ax = plt.subplots()
world.plot(ax=ax, figsize=(8, 8));

display(fig)

### Map plot overlays: Plotting multiple spatial layers

Here's a compact, quick way of using the GeoDataFrame plot method to overlay two GeoDataFrames while style customizing the styles for each layer.

In [64]:
'''Again, customized for Databricks' needs'''
fig, ax = plt.subplots()
oceans.plot(cmap='Set2', ax=ax, figsize=(10, 10));
world.plot(ax=ax, figsize=(8, 8));

display(fig)

We can also compose the plot using conventional `matplotlib` steps and options that give us more control.

In [66]:
f, ax = plt.subplots(1, figsize=(12, 6))
ax.set_title('Countries and Ocean Basins')
# Other nice categorical color maps (cmap) include 'Set2' and 'Set3'
oceans.plot(ax=ax, cmap='Paired')
world.plot(ax=ax, facecolor='lightgray', edgecolor='gray')
ax.set_ylim([-90, 90])
ax.set_axis_off()
plt.axis('equal');

display(f)

There is more in the original notebook, read it if you'd like.